In [2]:
import os
import shutil
import pydicom
import pandas as pd
from pathlib import Path

import numpy as np
import random

In [3]:
top = Path("CBIS-DDSM")

In [4]:
def new_name_dcm(dcm_path):


    try:
        ds = pydicom.dcmread(dcm_path)

        patient_id = ds.PatientID
        patient_id = patient_id.replace(".dcm", "")

        try:
            img_type = ds.SeriesDescription

            if "full" in img_type:
                new_name = patient_id + "_FULL" + ".dcm"
                print(f"FULL --- {new_name}")
                return new_name

            elif "crop" in img_type:

                suffix = patient_id.split("_")[-1]

                if suffix.isdigit():
                    new_patient_id = patient_id.split("_" + suffix)[0]
                    new_name = new_patient_id + "_CROP" + "_" + suffix + ".dcm"
                    print(f"CROP --- {new_name}")
                    return new_name

                elif not suffix.isdigit():
                    print(f"CROP ERROR, {patient_id}")
                    return False

            elif "mask" in img_type:

                suffix = patient_id.split("_")[-1]

                if suffix.isdigit():
                    new_patient_id = patient_id.split("_" + suffix)[0]
                    new_name = new_patient_id + "_MASK" + "_" + suffix + ".dcm"
                    print(f"MASK --- {new_name}")
                    return new_name

                elif not suffix.isdigit():
                    print(f"MASK ERROR, {patient_id}")
                    return False

        except:
            if "full" in dcm_path:
                new_name = patient_id + "_FULL" + ".dcm"
                return new_name

            else:
                arr = ds.pixel_array
                unique = np.unique(arr).tolist()

                if len(unique) != 2:

                    suffix = patient_id.split("_")[-1]

                    if suffix.isdigit():
                        new_patient_id = patient_id.split("_" + suffix)[0]
                        new_name = new_patient_id + "_CROP" + "_" + suffix + ".dcm"
                        print(f"CROP --- {new_name}")
                        return new_name

                    elif not suffix.isdigit():
                        print(f"CROP ERROR, {patient_id}")
                        return False

                elif len(unique) == 2:

                    suffix = patient_id.split("_")[-1]

                    if suffix.isdigit():
                        new_patient_id = patient_id.split("_" + suffix)[0]
                        new_name = new_patient_id + "_MASK" + "_" + suffix + ".dcm"
                        print(f"MASK --- {new_name}")
                        return new_name

                    elif not suffix.isdigit():
                        print(f"MASK ERROR, {patient_id}")
                        return False
                

    except Exception as e:
        print((f"Unable to new_name_dcm!\n{e}"))

In [5]:
def move_dcm_up(dest_dir, source_dir, dcm_filename):

    try:
        dest_dir_with_new_name = os.path.join(dest_dir, dcm_filename)

        if not os.path.exists(dest_dir_with_new_name):
            shutil.move(source_dir, dest_dir)

        elif os.path.exists(dest_dir_with_new_name):
            new_name_2 = dcm_filename.strip(".dcm") + "___a.dcm"
            shutil.move(source_dir, os.path.join(dest_dir, new_name_2))

    except Exception as e:
        print((f"Unable to move_dcm_up!\n{e}"))

In [6]:
def delete_empty_folders(top, error_dir):
    
    try:
        curdir_list = []
        files_list = []

        for (curdir, dirs, files) in os.walk(top=top, topdown=False):

            if curdir != str(top):

                dirs.sort()
                files.sort()

                print(f"WE ARE AT: {curdir}")
                print("=" * 10)

                print("List dir:")

                directories_list = [
                    f for f in os.listdir(curdir) if not f.startswith(".")
                ]
                print(directories_list)

                if len(directories_list) == 0:
                    print("DELETE")
                    shutil.rmtree(curdir, ignore_errors=True)

                elif len(directories_list) > 0:
                    print("DON'T DELETE")
                    curdir_list.append(curdir)
                    files_list.append(directories_list)

                print()
                print("Moving one folder up...")
                print("-" * 40)
                print()

        if len(curdir_list) > 0:
            not_empty_df = pd.DataFrame(
                list(zip(curdir_list, files_list)), columns=["curdir", "files"]
            )
            to_save_path = os.path.join(error_dir, "not-empty-folders.csv")
            not_empty_df.to_csv(to_save_path, index=False)

    except Exception as e:
        print((f"Unable to delete_empty_folders!\n{e}"))

In [7]:
def count_dcm(top):

    try:
        count = 0

        for _, _, files in os.walk(top):
            for f in files:
                if f.endswith(".dcm"):
                    count += 1

    except Exception as e:
        print((f"Unable to count_dcm!\n{e}"))

    return count


In [34]:
before = count_dcm(top=top)

In [35]:
for (curdir, dirs, files) in os.walk(top=top, topdown=False):
    dirs.sort()
    files.sort()
    for f in files:
        if f.endswith(".dcm"):
            old_name_path = os.path.join(curdir, f)
            new_name = new_name_dcm(dcm_path=old_name_path)
            if new_name:
                new_name_path = os.path.join(curdir, new_name)
                os.rename(old_name_path, new_name_path)
                move_dcm_up(
                        dest_dir=top, source_dir=new_name_path, dcm_filename=new_name
                    )

delete_empty_folders(top=top, error_dir=top)

after = count_dcm(top=top)

print(f"BEFORE --> Number of .dcm files: {before}")
print(f"AFTER --> Number of .dcm files: {after}")
print()
print("Getting out of extractDicom.")
print("-" * 30)

CROP --- Calc-Test_P_00038_LEFT_CC_CROP_1.dcm
MASK --- P_00038_LEFT_CC_MASK_1.dcm
CROP --- Calc-Test_P_00038_LEFT_MLO_CROP_1.dcm
MASK --- P_00038_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00038_RIGHT_CC_CROP_1.dcm
MASK --- P_00038_RIGHT_CC_MASK_1.dcm
CROP --- Calc-Test_P_00038_RIGHT_CC_CROP_2.dcm
MASK --- P_00038_RIGHT_CC_MASK_2.dcm
CROP --- Calc-Test_P_00038_RIGHT_MLO_CROP_1.dcm
MASK --- P_00038_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00038_RIGHT_MLO_CROP_2.dcm
MASK --- P_00038_RIGHT_MLO_MASK_2.dcm
CROP --- Calc-Test_P_00041_LEFT_CC_CROP_2.dcm
MASK --- P_00041_LEFT_CC_MASK_2.dcm
CROP --- Calc-Test_P_00041_LEFT_MLO_CROP_2.dcm
MASK --- P_00041_LEFT_MLO_MASK_2.dcm
CROP --- Calc-Test_P_00077_LEFT_CC_CROP_1.dcm
MASK --- P_00077_LEFT_CC_MASK_1.dcm
CROP --- Calc-Test_P_00077_LEFT_MLO_CROP_1.dcm
MASK --- P_00077_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00077_RIGHT_CC_CROP_1.dcm
MASK --- P_00077_RIGHT_CC_MASK_1.dcm
CROP --- Calc-Test_P_00077_RIGHT_CC_CROP_2.dcm
MASK --- P_00077_RIGHT_CC_MASK_

MASK --- P_00562_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00562_LEFT_MLO_CROP_2.dcm
MASK --- P_00562_LEFT_MLO_MASK_2.dcm
FULL --- Calc-Test_P_00562_RIGHT_CC_FULL.dcm
CROP --- Calc-Test_P_00562_RIGHT_CC_CROP_1.dcm
MASK --- P_00562_RIGHT_CC_MASK_1.dcm
FULL --- Calc-Test_P_00562_RIGHT_MLO_FULL.dcm
CROP --- Calc-Test_P_00562_RIGHT_MLO_CROP_1.dcm
MASK --- P_00562_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00570_LEFT_MLO_CROP_1.dcm
MASK --- P_00570_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00579_LEFT_MLO_CROP_1.dcm
MASK --- P_00579_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00589_LEFT_CC_CROP_1.dcm
MASK --- P_00589_LEFT_CC_MASK_1.dcm
CROP --- Calc-Test_P_00589_LEFT_MLO_CROP_1.dcm
MASK --- P_00589_LEFT_MLO_MASK_1.dcm
FULL --- Calc-Test_P_00608_LEFT_CC_FULL.dcm
CROP --- Calc-Test_P_00608_LEFT_CC_CROP_1.dcm
MASK --- P_00608_LEFT_CC_MASK_1.dcm
CROP --- Calc-Test_P_00608_LEFT_MLO_CROP_1.dcm
MASK --- P_00608_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_00620_LEFT_CC_CROP_1.dcm
MASK --- P_00620_LEFT_CC_MAS

MASK --- P_01211_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01211_RIGHT_MLO_CROP_2.dcm
MASK --- P_01211_RIGHT_MLO_MASK_2.dcm
CROP --- Calc-Test_P_01217_RIGHT_CC_CROP_1.dcm
MASK --- P_01217_RIGHT_CC_MASK_1.dcm
FULL --- Calc-Test_P_01217_RIGHT_MLO_FULL.dcm
CROP --- Calc-Test_P_01217_RIGHT_MLO_CROP_1.dcm
MASK --- P_01217_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01224_RIGHT_CC_CROP_1.dcm
MASK --- P_01224_RIGHT_CC_MASK_1.dcm
FULL --- Calc-Test_P_01224_RIGHT_MLO_FULL.dcm
CROP --- Calc-Test_P_01224_RIGHT_MLO_CROP_1.dcm
MASK --- P_01224_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01237_LEFT_CC_CROP_1.dcm
MASK --- P_01237_LEFT_CC_MASK_1.dcm
CROP --- Calc-Test_P_01237_LEFT_MLO_CROP_1.dcm
MASK --- P_01237_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01253_RIGHT_CC_CROP_1.dcm
MASK --- P_01253_RIGHT_CC_MASK_1.dcm
FULL --- Calc-Test_P_01253_RIGHT_MLO_FULL.dcm
CROP --- Calc-Test_P_01253_RIGHT_MLO_CROP_1.dcm
MASK --- P_01253_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01272_LEFT_CC_CROP_1.dcm
MASK --- P_01272

MASK --- P_01803_RIGHT_CC_MASK_1.dcm
CROP --- Calc-Test_P_01803_RIGHT_MLO_CROP_1.dcm
MASK --- P_01803_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01820_LEFT_MLO_CROP_1.dcm
MASK --- P_01820_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01834_LEFT_MLO_CROP_1.dcm
MASK --- P_01834_LEFT_MLO_MASK_1.dcm
FULL --- Calc-Test_P_01842_LEFT_MLO_FULL.dcm
CROP --- Calc-Test_P_01842_LEFT_MLO_CROP_1.dcm
MASK --- P_01842_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01845_RIGHT_CC_CROP_1.dcm
MASK --- P_01845_RIGHT_CC_MASK_1.dcm
CROP --- Calc-Test_P_01845_RIGHT_CC_CROP_2.dcm
MASK --- P_01845_RIGHT_CC_MASK_2.dcm
CROP --- Calc-Test_P_01845_RIGHT_MLO_CROP_1.dcm
MASK --- P_01845_RIGHT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01845_RIGHT_MLO_CROP_2.dcm
MASK --- P_01845_RIGHT_MLO_MASK_2.dcm
CROP --- Calc-Test_P_01861_LEFT_CC_CROP_1.dcm
MASK --- P_01861_LEFT_CC_MASK_1.dcm
FULL --- Calc-Test_P_01861_LEFT_MLO_FULL.dcm
CROP --- Calc-Test_P_01861_LEFT_MLO_CROP_1.dcm
MASK --- P_01861_LEFT_MLO_MASK_1.dcm
CROP --- Calc-Test_P_01867_LE

FULL --- Calc-Training_P_00019_RIGHT_MLO_FULL.dcm
CROP --- Calc-Training_P_00019_RIGHT_MLO_CROP_1.dcm
MASK --- Calc-Training_P_00019_RIGHT_MLO_MASK_1.dcm
FULL --- Calc-Training_P_00020_LEFT_CC_FULL.dcm
CROP --- Calc-Training_P_00020_LEFT_CC_CROP_1.dcm
MASK --- Calc-Training_P_00020_LEFT_CC_MASK_1.dcm
FULL --- Calc-Training_P_00020_LEFT_MLO_FULL.dcm
CROP --- Calc-Training_P_00020_LEFT_MLO_CROP_1.dcm
MASK --- Calc-Training_P_00020_LEFT_MLO_MASK_1.dcm
FULL --- Calc-Training_P_00022_LEFT_CC_FULL.dcm
CROP --- Calc-Training_P_00022_LEFT_CC_CROP_1.dcm
MASK --- Calc-Training_P_00022_LEFT_CC_MASK_1.dcm
FULL --- Calc-Training_P_00022_LEFT_MLO_FULL.dcm
CROP --- Calc-Training_P_00022_LEFT_MLO_CROP_1.dcm
MASK --- Calc-Training_P_00022_LEFT_MLO_MASK_1.dcm
FULL --- Calc-Training_P_00024_LEFT_CC_FULL.dcm
CROP --- Calc-Training_P_00024_LEFT_CC_CROP_1.dcm
MASK --- Calc-Training_P_00024_LEFT_CC_MASK_1.dcm
FULL --- Calc-Training_P_00024_LEFT_MLO_FULL.dcm
CROP --- Calc-Training_P_00024_LEFT_MLO_CROP_1.dcm


...

[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01494_LEFT_MLO\07-20-2016-DDSM-NA-87052\1.000000-full mammogram images-54678
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01494_LEFT_MLO\07-20-2016-DDSM-NA-87052
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01494_LEFT_MLO
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01494_LEFT_MLO_1\07-21-2016-DDSM-NA-89097\1.000000-ROI mask images-00638
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01494_LEFT_MLO_1\07-21-2016-DDSM-NA-89097
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01494_LEFT_MLO_1
Li

[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01593_LEFT_MLO
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01593_LEFT_MLO_1\07-21-2016-DDSM-NA-59372\1.000000-ROI mask images-65694
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01593_LEFT_MLO_1\07-21-2016-DDSM-NA-59372
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01593_LEFT_MLO_1
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01596_RIGHT_MLO\07-20-2016-DDSM-NA-96300\1.000000-full mammogram images-08112
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01596_RIGHT_MLO\07-20-2016-DDSM-NA-96300



Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01654_RIGHT_MLO\07-20-2016-DDSM-NA-54837
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01654_RIGHT_MLO
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01654_RIGHT_MLO_1\07-21-2016-DDSM-NA-35233\1.000000-ROI mask images-48198
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01654_RIGHT_MLO_1\07-21-2016-DDSM-NA-35233
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01654_RIGHT_MLO_1
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01656_LEFT_CC\07-20-2016-DDSM-NA-56813\1.000000-full mammogram images-45630
List dir

[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01745_RIGHT_MLO
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01745_RIGHT_MLO_1\07-21-2016-DDSM-NA-13131\1.000000-ROI mask images-14404
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01745_RIGHT_MLO_1\07-21-2016-DDSM-NA-13131
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01745_RIGHT_MLO_1
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01749_LEFT_CC\07-20-2016-DDSM-NA-45622\1.000000-full mammogram images-56192
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01749_LEFT_CC\07-20-2016-DDSM-NA-45622



Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01829_LEFT_MLO_1
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01831_RIGHT_CC\07-20-2016-DDSM-NA-40009\1.000000-full mammogram images-71383
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01831_RIGHT_CC\07-20-2016-DDSM-NA-40009
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01831_RIGHT_CC
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01831_RIGHT_CC_1\07-20-2016-DDSM-NA-86435\1.000000-cropped images-10446
List dir:
[]
DELETE

Moving one folder up...
----------------------------------------

WE ARE AT: CBIS-DDSM\Mass-Training_P_01831_RIGHT_CC_1\07-20-2016-DDSM-NA-86435
List dir:
[]


In [1]:
# This function was used because some of the calc_test files did not get named correctly

def rename_files(directory_path):
    # Get the list of files in the directory
    files = os.listdir(directory_path)

    for filename in files:
        # Get the full path of the file
        old_file_path = os.path.join(directory_path, filename)
        
        # Extract the file extension
        file_extension = os.path.splitext(filename)[1]
        
        # Construct the new file name
        new_filename = "Calc-Test_" + filename
        
        # Create the new file path
        new_file_path = os.path.join(directory_path, new_filename)
        
        # Rename the file
        os.rename(old_file_path, new_file_path)
        print(f"Renamed {filename} to {new_filename}")

In [ ]:
directory_path = "CBIS-DDSM/Calc/New folder"
rename_files(directory_path)

In [8]:
after = count_dcm(top=top)

In [9]:
after

10239